In [1]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import odeint, solve_ivp
import math
import pypower
from pypower.api import case9, ppoption, runpf, printpf
from copy import deepcopy

import pandas as pd


def dx_dt(x, t, fault_time, Y, V0, Pm, M):
    ps = 0

    for k in range(len(fault_time)):
        if t > fault_time[k]:
            ps = k + 1

    if t > 1:
        a = 0

    Ybus = Y[ps]
    Vg = V0 * np.exp(1j * x[0:3])
    Ibus = np.matmul(Ybus, Vg)
    S = np.conj(Ibus) * Vg
    Pe = np.real(S)
    dx = x[3:6]
    return np.hstack([dx, (Pm - Pe) / M])


def CalYbus(branch):
    Nbus = int(max([max(branch[:, 0]), max(branch[:, 1])]))
    Nbranch = len(branch[:, 0])
    Ybus = np.zeros([Nbus, Nbus])
    Ybus = np.complex_(Ybus)
    for k in range(Nbranch):
        N1 = int(branch[k, 0] - 1)
        N2 = int(branch[k, 1] - 1)
        YY = 1/(branch[k, 2]+1j*branch[k, 3])
        tap = branch[k, 8]
        if tap == 0:
            tap = 1

        tap = 1/tap
        Ybus[N1, N1] = Ybus[N1, N1] + tap * tap * YY + 1j * branch[k, 4]
        Ybus[N2, N2] = Ybus[N2, N2] + YY + 1j * branch[k, 4]
        Ybus[N1, N2] = Ybus[N1, N2] - tap * YY
        Ybus[N2, N1] = Ybus[N2, N1] - tap * YY
    return Ybus


def Ybus_aumentada(system): 
    result = pypower.api.runpf(system)[0]
    Nbus = int(max([max(system['branch'][:, 0]), max(system['branch'][:, 1])]))
    NG   = system['gen'][:, 0]
    Ngen = len(NG)
    Nload = system['bus'][[4, 6, 8], 0]
    NumC = len(Nload)
    YbusB = CalYbus(system['branch'])
    Ybus = np.zeros([Nbus + Ngen, Nbus + Ngen])
    Ybus = np.complex_(Ybus)
    Ybus[0:Nbus, 0:Nbus] = YbusB
    Vn = np.zeros([3, 1])
    Vn = np.complex_(Vn)
    for k in range(Ngen):
        n = int(NG[k]) - 1
        kk = k + Nbus
        xd = system['gen'][k, 21]
        yd = 1/(1j*xd)
        Ybus[n, n] = Ybus[n, n] + yd
        Ybus[kk, kk] = Ybus[kk, kk] + yd
        Ybus[kk, n] = Ybus[kk, n] - yd
        Ybus[n, kk] = Ybus[n, kk] - yd
        # generator internal voltage
        Vbus = result['bus'][n, 7] * (np.cos(result['bus'][n, 7] * math.pi / 180) + 1j * np.sin(result['bus'][n, 8] * math.pi/180))
        I = np.conj((result['gen'][n, 1] + 1j * result['gen'][n, 2]) / 100 / Vbus)
        Vn[k, 0] = Vbus + 1j*xd*I

    # convert loads to impedances and include them in the Ybus
    for k in range(NumC):
        n = int(Nload[k]) - 1
        S = (result['bus'][n, 2] + 1j * result['bus'][n, 3]) / 100
        Vbus = result['bus'][n, 7] * (np.cos(result['bus'][n, 7] * math.pi / 180) + 1j * np.sin(result['bus'][n, 7] * math.pi / 180))
        V = abs(Vbus)
        Y = np.conj(S/(V*V))
        Ybus[n, n] = Ybus[n, n] + Y
    return Ybus, Vn


def  Ybus_reduction(Ybus, NN, NR):
    Yg = Ybus[NN:NN+NR, NN:NN+NR]
    Yb = Ybus[NN:NN+NR, 0:NN]
    Yc = Ybus[0:NN, NN:NN+NR]
    Ye = Ybus[0:NN, 0:NN]
    Ybusr = Yg - Yb@np.linalg.inv(Ye)@Yc
    return Ybusr


def fault(Ybus, fault_branch):
    bus = np.arange(0, 12, 1)
    if fault_branch == 1:
        fault_bus = 3
    if fault_branch == 4:
        fault_bus = 5
    if fault_branch == 5:
        fault_bus = 7
    Ybus_fault = np.delete(Ybus, fault_bus, 0)
    Ybus_fault = np.delete(Ybus_fault, fault_bus, 1)
    return Ybus_fault


def post_fault_Ybus(system, fault_branch, Ybus):
    Ybusx =Ybus
    N1 = int(system['branch'][fault_branch,0]-1)
    N2 = int(system['branch'][fault_branch,1]-1)
    YY = 1/(system['branch'][fault_branch,2]+1j*system['branch'][fault_branch,3])
    bkm = system['branch'][fault_branch,4]
    tap = 1.0
    if tap==0:
        tap = 1.0
    tap = 1/tap
    Ybusx[N1,N1] = Ybusx[N1,N1] - tap*tap*YY - 1j*bkm
    Ybusx[N2,N2] = Ybusx[N2,N2] - YY         - 1j*bkm
    Ybusx[N1,N2] = Ybusx[N1,N2] + tap*YY
    Ybusx[N2,N1] = Ybusx[N2,N1] + tap*YY
    return Ybusx


def post_fault(system, fault_branch):
    case_new = deepcopy(system)
    branch_new = np.delete(case_new['branch'], fault_branch, axis=0)
    case_new['branch'] = branch_new
    return case_new 


def cal_stability(power_system, fault_branch):
    system = pypower.api.runpf(power_system)[0]
    #Inertia values for generator
    M = 2 * np.array([23.64, 6.80, 3.01]) / (2 * math.pi * 50) 
    #time(s):[short_circuit, open_time]
    fault_time = [0.1, 0.6] #play around with this to see when the stability improves
    
    Pm = system['gen'][:, 1] / 100
    t = np.linspace(0, 10, 1001) #reduce this from 10 

    Ybus, Vn = Ybus_aumentada(system)
    Y_nofault = Ybus_reduction(Ybus, 9, 3)

    Ybus_fault = fault(Ybus, fault_branch)
    Y_fault = Ybus_reduction(Ybus_fault, 8, 3)

    system_post_fault = post_fault(system, fault_branch)
    Ybus_post_fault, _ = Ybus_aumentada(system_post_fault)
    Y_post_fault = Ybus_reduction(Ybus_post_fault, 9, 3)


    Y = {0: Y_nofault,
         1: Y_fault,
         2: Y_post_fault}
    x0 = np.hstack([np.transpose(np.angle(Vn)), np.mat([0, 0, 0])]).tolist()[0]
    V0 = np.transpose(np.abs(Vn)).tolist()[0]

    x = odeint(dx_dt, x0, t, args=(fault_time, Y, V0, Pm, M))

    MT = sum(M)
    xcoi = np.zeros([len(x), 3]) #rotor angle values
    d_max = np.zeros(len(x))
    for k in range(len(x)):
        d = sum(x[k, 0:3] * M) / MT
        # w = sum(x[k, 3:6] * M) / MT
        xcoi[k, :] = x[k, 0:3] - [d, d, d]
        d_max[k] = max(xcoi[k, :]) - min(xcoi[k, :])

    return xcoi, max(d_max)*180/math.pi


#load the excel as pandas dataframe
bus_loads_imag = pd.read_excel('IEEE9bus_loads.xlsx', header=None, sheet_name='loads_imag')
bus_loads_imag = bus_loads_imag*100
bus_loads_imag = round(bus_loads_imag,2)

bus_loads_real = pd.read_excel('IEEE9bus_loads.xlsx', header=None, sheet_name='loads_real')
bus_loads_real = bus_loads_real*100
bus_loads_real = round(bus_loads_real,2)

d_max = [] #if d_mx is >180 its unstable
xcoi = []

# for row in range(1000): 
# #This simulation is for a single load. Loop through all the loads to calculate the stability index
#     power_system = pypower.api.runpf(pypower.api.case9())[0]
#     #Active power on load buses
#     power_system['bus'][[4, 6, 8], 2] = [56.28, 43.16, 127.68] #replace these with the page 1 values 
#     #Reactive power on load buses
#     power_system['bus'][[4, 6, 8], 3] = [27.34, 33.77, 45.25] #replace these with the page 2 values

#     fault_branch = 5 #is this constant? #try changing to see what happens #focus on one fault usually 

#     xcoi_temp, d_max_temp = cal_stability(power_system, fault_branch)
#     d_max.append(d_max_temp)
#     xcoi.append(xcoi)

# print(d_max)




In [2]:
d_max

[]

In [3]:
xcoi

[]

In [4]:
stable_pnts = ([x for x in d_max if x<=180]) #stable points

In [5]:
indexes = []
for j in stable_pnts:
    indexes.append(d_max.index(j))

In [6]:
len(indexes)

0

In [14]:
stable_bus_loads_real = []
for i in indexes:
    stable_bus_loads_real.append([bus_loads_real[0][i], bus_loads_real[1][i], bus_loads_real[2][i]])

stable_bus_loads_real

549

In [16]:
stable_bus_loads_real = pd.DataFrame(stable_bus_loads_real)

In [17]:
stable_bus_loads_real

0       1       2
0     94.44  139.39  126.20
1     98.12  147.92  165.88
2     87.79  138.81  112.39
3    108.61  138.05   92.41
4    103.48  127.66  169.91
..      ...     ...     ...
544  123.45  123.08  145.18
545   64.24  108.04  162.63
546  132.70   73.26  167.36
547  127.30   81.87  128.36
548   69.49   98.46  132.15

[549 rows x 3 columns]

In [18]:
stable_bus_loads_imag = []
for i in indexes:
    stable_bus_loads_imag.append([bus_loads_imag[0][i], bus_loads_imag[1][i], bus_loads_imag[2][i]])

stable_bus_loads_imag = pd.DataFrame(stable_bus_loads_imag)

In [19]:
stable_bus_loads_imag

0      1      2
0    26.18  34.31  56.51
1    25.03  34.60  52.66
2    28.79  35.65  49.67
3    24.54  30.66  57.42
4    32.86  31.42  52.64
..     ...    ...    ...
544  26.12  37.34  55.18
545  25.47  40.88  56.49
546  30.40  37.64  44.41
547  26.83  32.83  47.05
548  24.32  41.66  50.44

[549 rows x 3 columns]

In [21]:
with pd.ExcelWriter('Stable_Loads.xlsx') as writer:  
    stable_bus_loads_real.to_excel(writer, sheet_name='loads_real', header=False, index=False)
    stable_bus_loads_imag.to_excel(writer, sheet_name='loads_imag', header=False, index=False)

In [23]:
unstable_bus_loads_real = bus_loads_real.drop(indexes)
unstable_bus_loads_imag = bus_loads_imag.drop(indexes)

In [24]:
with pd.ExcelWriter('Unstable_Loads.xlsx') as writer:  
    unstable_bus_loads_real.to_excel(writer, sheet_name='loads_real', header=False, index=False)
    unstable_bus_loads_imag.to_excel(writer, sheet_name='loads_imag', header=False, index=False)

#  TEST UNSTABLE POINTS

In [2]:
unstable_bus_loads_gen1 = pd.read_excel('Unstable0_6s_Points_Gen.xlsx', sheet_name='gen1')
unstable_bus_loads_gen2 = pd.read_excel('Unstable0_6s_Points_Gen.xlsx', sheet_name='gen2')
unstable_bus_loads_gen3 = pd.read_excel('Unstable0_6s_Points_Gen.xlsx', sheet_name='gen3')
unstable_bus_loads_gen1

Rotor Angle  Active Power  Voltage Mag  stable  Rotor Angle (scaled)  \
0       0.456365         85.48     0.980714       0              0.267162   
1       0.494351         91.98     0.979973       0              0.427669   
2       0.484198         59.66     0.977993       0              0.384766   
3       0.493243         75.40     0.986590       0              0.422988   
4       0.439340         51.31     0.992769       0              0.195221   
..           ...           ...          ...     ...                   ...   
446     0.450358         56.60     0.990453       0              0.241779   
447     0.511248         47.14     0.988251       0              0.499068   
448     0.469914         93.84     0.975624       0              0.324409   
449     0.409675        124.96     0.974978       0              0.069872   
450     0.438569        106.52     0.978015       0              0.191964   

     Voltage Mag (scaled)  Predicted Active Power scaled  \
0                0.538205                     107.155228   
1                0.515481                     110.493359   
2                0.454812                     113.118054   
3                0.718272                      89.377875   
4                0.907658                     -31.735377   
..                    ...                            ...   
446              0.836671                      26.594235   
447              0.769193                      82.738162   
448              0.382193                     115.174289   
449              0.362414                     113.237201   
450              0.455484                     111.270557   

     Predicted Active Power  
0                 68.328288  
1                 71.373686  
2                 77.185241  
3                 51.006972  
4                 30.368391  
..                      ...  
446               37.981384  
447               46.183632  
448               84.045420  
449               84.460613  
450               76.113289  

[451 rows x 8 columns]

In [3]:
unstable_bus_loads_gen3

Rotor Angle  Active Power  Voltage Mag  stable  Rotor Angle (scaled)  \
0       2.371056        117.59     0.971823       0              0.737806   
1       2.487595         92.53     0.971354       0              0.810373   
2       2.241416        157.99     0.954855       0              0.657082   
3       2.388489        120.44     0.970884       0              0.748661   
4       2.609487        111.82     0.976770       0              0.886272   
..           ...           ...          ...     ...                   ...   
446     2.470732        132.53     0.966038       0              0.799872   
447     2.729880         67.14     0.981787       0              0.961238   
448     2.284974        128.02     0.956250       0              0.684205   
449     2.505535         65.18     0.964546       0              0.821543   
450     2.483243         79.92     0.975904       0              0.807662   

     Voltage Mag (scaled)  Predicted Active Power  \
0                0.608781              175.116616   
1                0.594830              164.198263   
2                0.104020              194.588918   
3                0.580847              173.811330   
4                0.755943              150.623800   
..                    ...                     ...   
446              0.436693              168.255632   
447              0.905185              138.007791   
448              0.145529              189.851383   
449              0.392322              165.863515   
450              0.730195              162.428387   

     Predicted Active Power scaled  
0                       147.835747  
1                       145.910720  
2                       165.019898  
3                       149.867777  
4                       120.498915  
..                             ...  
446                     155.644855  
447                      79.202311  
448                     164.034200  
449                     155.788972  
450                     129.506866  

[451 rows x 8 columns]

In [3]:
unstable_bus_loads_imag = pd.read_excel('Unstable_Loads.xlsx', header=None, sheet_name='loads_imag')
unstable_bus_loads_imag

0      1      2
0    32.18  36.54  42.93
1    32.16  29.08  49.18
2    34.25  38.35  51.24
3    27.34  33.77  45.25
4    25.95  40.77  40.47
..     ...    ...    ...
446  24.98  35.43  49.42
447  34.02  40.25  41.24
448  31.61  28.54  58.28
449  24.77  41.20  58.39
450  31.16  37.96  44.35

[451 rows x 3 columns]

In [18]:
unstable_pred_AP = []

for e in range (len(unstable_bus_loads_gen1['Predicted Active Power'])):
    unstable_pred_AP.append([unstable_bus_loads_gen1['Predicted Active Power'][e], unstable_bus_loads_gen2['Predicted Active Power'][e], unstable_bus_loads_gen3['Predicted Active Power'][e]])

unstable_pred_AP


[[68.3282876243162, 152.71375826114, 300.8703289291629],
 [71.37368567523538, 149.1035272851506, 300.8543150493578],
 [77.18524136443614, 150.316530709946, 302.0656724243531],
 [51.00697215323328, 149.371120064747, 300.2692822762417],
 [30.36839126099824, 155.0597126299247, 294.624054460414],
 [73.07810719733118, 151.7181931253954, 300.6318668433588],
 [68.42241379295467, 148.4401947847154, 303.2702042878151],
 [65.24181839500545, 155.2245261469058, 297.2551554408297],
 [75.00643423994063, 148.0316958229572, 300.0867251939806],
 [49.80303583529769, 154.6108999836846, 299.024853794219],
 [73.46335115891873, 154.006078019893, 300.7465646182521],
 [57.21255928141056, 151.6870722554892, 298.5020745569965],
 [58.90076813709913, 154.5289908504545, 301.408123670337],
 [101.5775302746612, 151.0614543417755, 306.4475750754669],
 [69.59875928101121, 153.2330355678075, 299.1745162305696],
 [51.38519770142614, 154.8860254755238, 299.0069370098597],
 [54.74645037812172, 150.9328300135557, 301.42111

In [19]:
unstable_bus_loads_imag[1][1]

29.08

In [20]:
d_max = [] #if d_mx is >180 its unstable
xcoi = []

for row in range(451): 
#This simulation is for a single load. Loop through all the loads to calculate the stability index
    power_system = pypower.api.runpf(pypower.api.case9())[0]
    #Active power on load buses
    power_system['bus'][[4, 6, 8], 2] = [unstable_pred_AP[row][0], unstable_pred_AP[row][1], unstable_pred_AP[row][2]] #replace these with the page 1 values 
    #Reactive power on load buses
    power_system['bus'][[4, 6, 8], 3] = [unstable_bus_loads_imag[0][row], unstable_bus_loads_imag[1][row], unstable_bus_loads_imag[2][row]] #replace these with the page 2 values

    fault_branch = 5 #is this constant? #try changing to see what happens #focus on one fault usually 

    xcoi_temp, d_max_temp = cal_stability(power_system, fault_branch)
    d_max.append(d_max_temp)
    xcoi.append(xcoi)

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.04 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.04 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.03 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.07 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 


Newton's method power flow converged in 4 iterations.

Converged in 0.07 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    518.0             208.3
Loads              3     Load                   500.6             106.4
  Fixed            3       Fixed                500.6             106.4
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           8     Losses (I^2 * Z)        17.37            209.38
Transformers       0     Branch Charging (inj)     -              107.5
Inter-ties         0   

...

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.03 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.05 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.03 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.04 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.03 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

In [21]:
len(d_max)

451

In [22]:
stable_pnts = ([x for x in d_max if x<=180]) #stable points

In [23]:
len(stable_pnts)

451

In [24]:
indexes = []
for j in stable_pnts:
    indexes.append(d_max.index(j))

In [25]:
len(indexes)

451

In [26]:
indexes

[0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 139,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 173,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,


In [27]:
# unstable_bus_loads_gen1 = unstable_bus_loads_gen1.drop(columns=['stabilised'])

In [28]:
unstable_bus_loads_gen1

Rotor Angle  Active Power  Voltage Mag  stable  Rotor Angle (scaled)  \
0       0.456365         85.48     0.980714       0              0.267162   
1       0.494351         91.98     0.979973       0              0.427669   
2       0.484198         59.66     0.977993       0              0.384766   
3       0.493243         75.40     0.986590       0              0.422988   
4       0.439340         51.31     0.992769       0              0.195221   
..           ...           ...          ...     ...                   ...   
446     0.450358         56.60     0.990453       0              0.241779   
447     0.511248         47.14     0.988251       0              0.499068   
448     0.469914         93.84     0.975624       0              0.324409   
449     0.409675        124.96     0.974978       0              0.069872   
450     0.438569        106.52     0.978015       0              0.191964   

     Voltage Mag (scaled)  Predicted Active Power scaled  \
0                0.538205                     107.155228   
1                0.515481                     110.493359   
2                0.454812                     113.118054   
3                0.718272                      89.377875   
4                0.907658                     -31.735377   
..                    ...                            ...   
446              0.836671                      26.594235   
447              0.769193                      82.738162   
448              0.382193                     115.174289   
449              0.362414                     113.237201   
450              0.455484                     111.270557   

     Predicted Active Power  stabilised scaled  
0                 68.328288                  1  
1                 71.373686                  1  
2                 77.185241                  1  
3                 51.006972                  1  
4                 30.368391                  0  
..                      ...                ...  
446               37.981384                  1  
447               46.183632                  0  
448               84.045420                  1  
449               84.460613                  1  
450               76.113289                  1  

[451 rows x 9 columns]

In [29]:
unstable_bus_loads_gen1['stabilised'] = 0

for j in range (len(unstable_bus_loads_gen1['Predicted Active Power'])):
    if j in indexes:
        unstable_bus_loads_gen1['stabilised'][j] = int(1)
    else:
        unstable_bus_loads_gen1['stabilised'][j] = int(0)
        
unstable_bus_loads_gen1

<ipython-input-29-7c58b730f7cc>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  unstable_bus_loads_gen1['stabilised'][j] = int(1)


Rotor Angle  Active Power  Voltage Mag  stable  Rotor Angle (scaled)  \
0       0.456365         85.48     0.980714       0              0.267162   
1       0.494351         91.98     0.979973       0              0.427669   
2       0.484198         59.66     0.977993       0              0.384766   
3       0.493243         75.40     0.986590       0              0.422988   
4       0.439340         51.31     0.992769       0              0.195221   
..           ...           ...          ...     ...                   ...   
446     0.450358         56.60     0.990453       0              0.241779   
447     0.511248         47.14     0.988251       0              0.499068   
448     0.469914         93.84     0.975624       0              0.324409   
449     0.409675        124.96     0.974978       0              0.069872   
450     0.438569        106.52     0.978015       0              0.191964   

     Voltage Mag (scaled)  Predicted Active Power scaled  \
0                0.538205                     107.155228   
1                0.515481                     110.493359   
2                0.454812                     113.118054   
3                0.718272                      89.377875   
4                0.907658                     -31.735377   
..                    ...                            ...   
446              0.836671                      26.594235   
447              0.769193                      82.738162   
448              0.382193                     115.174289   
449              0.362414                     113.237201   
450              0.455484                     111.270557   

     Predicted Active Power  stabilised scaled  stabilised  
0                 68.328288                  1           1  
1                 71.373686                  1           1  
2                 77.185241                  1           1  
3                 51.006972                  1           1  
4                 30.368391                  0           1  
..                      ...                ...         ...  
446               37.981384                  1           1  
447               46.183632                  0           1  
448               84.045420                  1           1  
449               84.460613                  1           1  
450               76.113289                  1           1  

[451 rows x 10 columns]

In [31]:
count_1=0
count_0=0
for j in range (len(unstable_bus_loads_gen1['Predicted Active Power'])):
    if unstable_bus_loads_gen1['Predicted Active Power'][j] < 0:
        if unstable_bus_loads_gen1['stabilised'][j] == 1:
            count_1 +=1
        else:
            count_0 +=1
print(count_1)
print(count_0)

0
0


In [32]:
with pd.ExcelWriter('Unstable0_6s_Points_Gen.xlsx') as writer:  
    unstable_bus_loads_gen1.to_excel(writer, sheet_name='gen1', header=True, index=False)
    unstable_bus_loads_gen2.to_excel(writer, sheet_name='gen2', header=True, index=False)
    unstable_bus_loads_gen3.to_excel(writer, sheet_name='gen3', header=True, index=False)
#     unstable_bus_loads_imag.to_excel(writer, sheet_name='loads_imag', header=False, index=False)